In [1]:
%pip install -q ultralytics
%pip install -q opencv-python-headless


[notice] A new release of pip is available: 23.2.1 -> 23.3.1
[notice] To update, run: python3 -m pip install --upgrade pip


In [ ]:
import zipfile
from tqdm import tqdm

fname = '/home/jupyter/datasphere/project/train_dataset_train.zip'
path = './'

with zipfile.ZipFile(fname, 'r') as zf:
    for entry in tqdm(zf.infolist(), desc='Extracting '):
        try:
            zf.extract(entry, path)
        except zipfile.error as e:
            pass


Extracting :  86%|████████▌ | 859/999 [06:39<04:11,  1.79s/it]

In [2]:
import os
from ultralytics import YOLO
import cv2
from tqdm import tqdm

# Обучение модели для выбора кадра

In [4]:
model = YOLO('yolov8n-cls.pt')

100%|██████████| 5.28M/5.28M [00:00<00:00, 19.6MB/s]


In [ ]:
results = model.train(data='detect_shots.yaml', epochs=20, imgsz=640)

# Извлечение кадров

In [9]:
# shot_model = YOLO('artefacts/shots_detector_run2.pt')
shot_model = YOLO('../artefacts/shots_detector_run2.pt')
names = shot_model.names

In [38]:
# Функция для конвертации времени в формате чч:мм:сс в количество секунд
def convert_time_to_seconds(time_str):
    h, m, s = map(int, time_str.split(':'))
    return h * 3600 + m * 60 + s


# train_dir = "/home/jupyter/datasphere/project/train"
# train_shots_dir = "/home/jupyter/datasphere/project/train_shots"
train_dir = "../data/train"
train_shots_dir = "../data/train_shots"
os.makedirs(train_shots_dir, exist_ok=True)

folders = os.listdir(train_dir)
folders.sort()

for folder in folders:
    os.makedirs(os.path.join(train_shots_dir, folder), exist_ok=True)
    
    video_files = os.listdir(os.path.join(train_dir, folder))
    for video_file in tqdm(video_files):
        try:
            # Загрузите видео
            video_path = os.path.join(train_dir, folder, video_file)
            cap = cv2.VideoCapture(video_path)

            # Убедитесь, что видео было успешно загружено
            if not cap.isOpened():
                raise Exception("Error opening video file")
            
            fps = cap.get(cv2.CAP_PROP_FPS)      # OpenCV v2.x used "CV_CAP_PROP_FPS"
            frame_count = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
            duration = frame_count/fps
            
            if duration < 220:
                continue

            # Вычислите номера кадров для начального и конечного времени
            start_time = convert_time_to_seconds('00:01:40')
            end_time = convert_time_to_seconds('00:02:30')
            start_frame = int(start_time * fps)
            end_frame = int(end_time * fps)

            # Установите начальную позицию видео
            cap.set(cv2.CAP_PROP_POS_FRAMES, start_frame)

            i = 0
            step = 10
            # Читайте видео с начальной до конечной позиции
            while cap.get(cv2.CAP_PROP_POS_FRAMES) < end_frame:
                ret, frame = cap.read()
                # Проверьте, успешно ли прочитан кадр
                if not ret:
                    break

                if i % step == 0:
                    res = shot_model.predict(frame)[0].probs
                    
                    if names[res.top1] == 'bad':
                        continue
                    
                    frame_number = int(cap.get(cv2.CAP_PROP_POS_FRAMES))
                    frame_name = os.path.join(train_shots_dir, folder, f'{os.path.split(video_file)[1]}_frame_{frame_number}.jpg')
                    if os.path.exists(frame_name):
                        break
                    is_success, im_buf_arr = cv2.imencode(".jpg", frame)
                    if not is_success:
                        raise Exception("cv2.imencode doesn't work")
                    im_buf_arr.tofile(frame_name)
                    
                
                i += 1

            # Освободите захват видео и закройте все окна
            cap.release()
        except Exception as e:
            print(e)
            pass
cv2.destroyAllWindows()

  0%|          | 0/250 [00:00<?, ?it/s]


0: 640x640 bad 1.00, good 0.00, 106.0ms
Speed: 9.0ms preprocess, 106.0ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 87.0ms
Speed: 7.0ms preprocess, 87.0ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 87.0ms
Speed: 9.0ms preprocess, 87.0ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 91.0ms
Speed: 10.0ms preprocess, 91.0ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 93.0ms
Speed: 10.0ms preprocess, 93.0ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 110.0ms
Speed: 13.0ms preprocess, 110.0ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 104.0ms
Speed: 11.0ms preprocess, 104.0ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00

  0%|          | 1/250 [01:03<4:23:09, 63.41s/it]


0: 640x640 bad 1.00, good 0.00, 139.0ms
Speed: 12.0ms preprocess, 139.0ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 120.0ms
Speed: 14.0ms preprocess, 120.0ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 131.0ms
Speed: 10.0ms preprocess, 131.0ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 141.0ms
Speed: 12.0ms preprocess, 141.0ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 117.0ms
Speed: 14.0ms preprocess, 117.0ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 119.0ms
Speed: 14.0ms preprocess, 119.0ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 99.0ms
Speed: 10.0ms preprocess, 99.0ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, 

  1%|          | 2/250 [02:42<5:48:09, 84.23s/it]

...


0: 640x640 bad 1.00, good 0.00, 119.0ms
Speed: 10.0ms preprocess, 119.0ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 116.0ms
Speed: 9.0ms preprocess, 116.0ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 125.0ms
Speed: 131.0ms preprocess, 125.0ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 97.0ms
Speed: 13.0ms preprocess, 97.0ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 100.0ms
Speed: 11.0ms preprocess, 100.0ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 106.0ms
Speed: 12.0ms preprocess, 106.0ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 106.0ms
Speed: 23.0ms preprocess, 106.0ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, 

 33%|███▎      | 82/250 [1:18:22<2:47:10, 59.71s/it]


0: 640x640 bad 1.00, good 0.00, 152.0ms
Speed: 10.0ms preprocess, 152.0ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 97.0ms
Speed: 11.0ms preprocess, 97.0ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 91.0ms
Speed: 9.0ms preprocess, 91.0ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 229.0ms
Speed: 11.0ms preprocess, 229.0ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 96.0ms
Speed: 11.0ms preprocess, 96.0ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 95.0ms
Speed: 10.0ms preprocess, 95.0ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00, 98.0ms
Speed: 7.0ms preprocess, 98.0ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 640)

0: 640x640 bad 1.00, good 0.00,

 33%|███▎      | 82/250 [1:19:23<2:42:39, 58.09s/it]


KeyboardInterrupt: 